In [30]:
import requests
import pandas as pd
import xmltodict
from os import name
import xml.etree.ElementTree as et
import bs4
from lxml import html
from urllib.parse import urlencode, quote_plus, unquote

url = "https://safemap.go.kr/openApiService/data/getCrmnlStatsMurderData.do"
params = {
"serviceKey": "",
"numOfRows": "3000",
"pageNo": "1",
"dataType": "xml"
}

response = requests.get(url, params=params)
content = response.text

xml_obj = bs4.BeautifulSoup(content,'lxml-xml')
rows = xml_obj.findAll('item')

row_list = [] # 행값
name_list = [] # 열이름값
value_list = [] #데이터값

# xml 안의 데이터 수집
for i in range(0, len(rows)):
    columns = rows[i].find_all()
    #첫째 행 데이터 수집
    for j in range(0,len(columns)):
        if i ==0:
            # 컬럼 이름 값 저장
            name_list.append(columns[j].name)
        # 컬럼의 각 데이터 값 저장
        value_list.append(columns[j].text)
    # 각 행의 value값 전체 저장
    row_list.append(value_list)
    # 데이터 리스트 값 초기화
    value_list=[]

#xml값 DataFrame으로 만들기
df = pd.DataFrame(row_list, columns=name_list)
df

OBJT_ID POLC_NM POLC_SE PLCSTN_NM MURDER CTPRVN_NM SGG_KOR_NM CTPRVN_CD  \
0          1    서울서부  01_경찰서     형사지원팀      1     서울특별시        은평구        11   
1          2   서울영등포  01_경찰서  다목적기동순찰대      1     서울특별시       영등포구        11   
2          3    서울강남  01_경찰서  다목적기동순찰대      1     서울특별시        강남구        11   
3          4    부산동부  01_경찰서      형사1팀      1     부산광역시         동구        26   
4          5    대전둔산  01_경찰서  다목적기동순찰대      1     대전광역시         서구        30   
...      ...     ...     ...       ...    ...       ...        ...       ...   
2037    2038     서귀포  03_파출소        대정      3   제주특별자치도       서귀포시        50   
2038    2039     서귀포  03_파출소        중문      2   제주특별자치도       서귀포시        50   
2039    2040     서귀포  03_파출소        대신      3   제주특별자치도       서귀포시        50   
2040    2041     서귀포  03_파출소        효돈      1   제주특별자치도       서귀포시        50   
2041    2042    대전동부  02_지구대      대전역전      2     대전광역시         동구        30   

     SGG_CD                 X                 Y  
0     11380     14128814.2085     4523368.85601  
1     11560     14126536.9234     4512701.85245  
2     11680     14145045.9595     4510321.54401  
3     26170     14365688.5262     4181553.41277  
4     30170     14179932.5417     4350045.11408  
...     ...               ...               ...  
2037  50130      14054773.656     3924933.67007  
2038  50130     14073291.4084     3928849.47696  
2039  50130     14082991.9892     3929113.79376  
2040  50130     14094955.7175     3930378.55343  
2041  30110  14185874.8206542  4346266.53276275  

[2042 rows x 11 columns]

In [31]:
df.set_index("OBJT_ID",inplace=True)

In [32]:
df

POLC_NM POLC_SE PLCSTN_NM MURDER CTPRVN_NM SGG_KOR_NM CTPRVN_CD  \
OBJT_ID                                                                   
1          서울서부  01_경찰서     형사지원팀      1     서울특별시        은평구        11   
2         서울영등포  01_경찰서  다목적기동순찰대      1     서울특별시       영등포구        11   
3          서울강남  01_경찰서  다목적기동순찰대      1     서울특별시        강남구        11   
4          부산동부  01_경찰서      형사1팀      1     부산광역시         동구        26   
5          대전둔산  01_경찰서  다목적기동순찰대      1     대전광역시         서구        30   
...         ...     ...       ...    ...       ...        ...       ...   
2038        서귀포  03_파출소        대정      3   제주특별자치도       서귀포시        50   
2039        서귀포  03_파출소        중문      2   제주특별자치도       서귀포시        50   
2040        서귀포  03_파출소        대신      3   제주특별자치도       서귀포시        50   
2041        서귀포  03_파출소        효돈      1   제주특별자치도       서귀포시        50   
2042       대전동부  02_지구대      대전역전      2     대전광역시         동구        30   

        SGG_CD                 X                 Y  
OBJT_ID                                             
1        11380     14128814.2085     4523368.85601  
2        11560     14126536.9234     4512701.85245  
3        11680     14145045.9595     4510321.54401  
4        26170     14365688.5262     4181553.41277  
5        30170     14179932.5417     4350045.11408  
...        ...               ...               ...  
2038     50130      14054773.656     3924933.67007  
2039     50130     14073291.4084     3928849.47696  
2040     50130     14082991.9892     3929113.79376  
2041     50130     14094955.7175     3930378.55343  
2042     30110  14185874.8206542  4346266.53276275  

[2042 rows x 10 columns]

In [5]:
import firebase_admin
from firebase_admin import credentials
from firebase_admin import firestore
import json
import pandas as pd

# Firebase 서비스 계정 키 파일 경로
cred = credentials.Certificate(".json")

# Firebase 앱 초기화
firebase_admin.initialize_app(cred)

db = firestore.client()

ValueError: The default Firebase app already exists. This means you called initialize_app() more than once without providing an app name as the second argument. In most cases you only need to call initialize_app() once. But if you do want to initialize multiple apps, pass a second argument to initialize_app() to give each app a unique name.

In [33]:
for col in df.columns:
    doc_ref=db.collection('crime').document(col)
    doc_ref.set(df[col].to_dict())

In [18]:
docs=db.collection('crime').stream()
data={}
for doc in docs:
    data[doc.id]=dict(sorted(doc.to_dict().items())).values()
sorted_df=pd.DataFrame(data, index=dict(sorted(doc.to_dict().items())).keys())
sorted_df

CTPRVN_CD CTPRVN_NM MURDER PLCSTN_NM POLC_NM POLC_SE SGG_CD SGG_KOR_NM  \
1           11     서울특별시      1     형사지원팀    서울서부  01_경찰서  11380        은평구   
10          48      경상남도      1      형사4팀    마산중부  01_경찰서  48125  창원시 마산합포구   
100         11     서울특별시      3        도곡    서울수서  02_지구대  11680        강남구   
1000        41       경기도      3        금곡   남양주남부  03_파출소  41360       남양주시   
1001        41       경기도      2       다산1   남양주남부  03_파출소  41360       남양주시   
...        ...       ...    ...       ...     ...     ...    ...        ...   
995         41       경기도      3        가좌    일산서부  03_파출소  41287   고양시 일산서구   
996         41       경기도      2        수택      구리  03_파출소  41310        구리시   
997         41       경기도      5        화도   남양주남부  03_파출소  41360       남양주시   
998         41       경기도      2        천마   남양주남부  03_파출소  41360       남양주시   
999         41       경기도      1        진접   남양주북부  03_파출소  41360       남양주시   

                  X              Y  
1     14128814.2085  4523368.85601  
10    14311694.2206  4190028.90847  
100   14142441.9183  4509218.02792  
1000  14160897.3541   4527902.6258  
1001  14155619.1011  4524289.59293  
...             ...            ...  
995   14106767.9288  4535912.91489  
996   14153958.2202  4522579.05096  
997    14171607.803  4530142.41723  
998   14169480.9328  4531466.81391  
999   14158064.8853   4539953.0936  

[2042 rows x 10 columns]

In [5]:
import requests
import pandas as pd
import xmltodict
from os import name
import xml.etree.ElementTree as et
import bs4
from lxml import html
from urllib.parse import urlencode, quote_plus, unquote

df1=pd.DataFrame()

gugun=[1116,1117,1124,1111,1115,1123,1112,1125,1122,1107,1105,1114,1110,1109,1119,1104,1106,1118,1120,1113,1103,1108,1101,1102,1121,1212,1211,1216,1207,1203,1206,1208,1215,1210,1202,1214,1213,1204,1201,1205,1209,2204,2207,2208,2202,2205,2203,2206,2201,2309,2308,2303,2305,2302,2304,2306,2307,2310,2301,2404,2405,2401,2403,2402,2505,2501,2503,2504,2502,2602,2603,2604,2605,2601,2701,1322,1318,1332,1309,1319,1310,1333,1327,1334,1330,1306,1303,1302,1316,1307,1326,1305,1311,1323,1313,1320,1335,1325,1336,1304,1324,1317,1308,1321,1337,1315,1404,1422,1403,1407,1405,1420,1423,1415,1402,1421,1417,1418,1401,1406,1416,1412,1419,1413,1516,1520,1512,1514,1513,1517,1503,1521,1515,1511,1501,1502,1624,1605,1611,1615,1623,1604,1616,1606,1617,1603,1613,1621,1602,1619,1612,1620,1719,1702,1706,1705,1713,1720,1717,1711,1723,1715,1714,1701,1704,1712,1822,1818,1813,1808,1814,1806,1812,1802,1825,1819,1804,1832,1803,1828,1824,1830,1829,1821,1831,1827,1823,1820,1935,1903,1923,1906,1912,1904,1909,1932,1910,1924,1905,1917,1916,1907,1908,1930,1934,1933,1913,1922,1915,1925,1902,2010,2028,2022,2008,2024,2009,2023,2026,2016,2012,2003,2014,2030,2006,2025,2013,2027,2029,2102,2101]
url = "https://opendata.koroad.or.kr/data/rest/accident/death?authKey="
for i in gugun:
    params = {
    "searchYear":"2022",
    "sido":i-(i%100),
    "gugun":i,
    }
    response = requests.get(url, params=params)    

    xml_obj = bs4.BeautifulSoup(response.text,'lxml-xml')
    rows = xml_obj.findAll('item')

    row_list = [] # 행값
    name_list = [] # 열이름값
    value_list = [] #데이터값

    # xml 안의 데이터 수집
    for i in range(0, len(rows)):
        columns = rows[i].find_all()
        #첫째 행 데이터 수집
        for j in range(0,len(columns)):
            if i ==0:
                # 컬럼 이름 값 저장
                name_list.append(columns[j].name)
            # 컬럼의 각 데이터 값 저장
            value_list.append(columns[j].text)
        # 각 행의 value값 전체 저장
        row_list.append(value_list)
        # 데이터 리스트 값 초기화
        value_list=[]

    #xml값 DataFrame으로 만들기
    df = pd.DataFrame(row_list, columns=name_list)
    df1=pd.concat([df1,df])
df1

acc_year  occrrnc_dt dght_cd occrrnc_day_cd dth_dnv_cnt injpsn_cnt  \
0      2022  2022021101       2              6           1          1   
1      2022  2022030919       2              4           1          1   
2      2022  2022031920       2              7           1          1   
3      2022  2022032606       1              7           1          2   
4      2022  2022040701       2              5           1          1   
..      ...         ...     ...            ...         ...        ...   
31     2022  2022110618       2              1           1          1   
32     2022  2022110908       1              4           1          1   
33     2022  2022111515       1              3           1          1   
34     2022  2022121909       1              2           1          1   
35     2022  2022122007       1              3           1          1   

   se_dnv_cnt sl_dnv_cnt wnd_dnv_cnt occrrnc_lc_sido_cd  ... acc_ty_cd  \
0           0          0           0               1100  ...        05   
1           0          0           0               1100  ...        22   
2           0          0           0               1100  ...        23   
3           1          0           0               1100  ...        22   
4           0          0           0               1100  ...        05   
..        ...        ...         ...                ...  ...       ...   
31          0          0           0               2100  ...        01   
32          0          0           0               2100  ...        32   
33          0          0           0               2100  ...        25   
34          0          0           0               2100  ...        05   
35          0          0           0               2100  ...        02   

   aslt_vtr_cd road_frm_lclas_cd road_frm_cd wrngdo_isrty_vhcty_lclas_cd  \
0          05                 01          05                          01   
1          03                 02          06                          02   
2          99                 01          05                          01   
3          03                 02          06                          02   
4          99                 02          06                          05   
..         ...               ...         ...                         ...   
31         99                 01          05                          03   
32         05                 01          05                          03   
33         05                 01          05                          03   
34         05                 01          05                          10   
35         05                 02          06                          03   

   dmge_isrty_vhcty_lclas_cd occrrnc_lc_x_crd occrrnc_lc_y_crd        lo_crd  \
0                         12         962220           1943733   127.07262264   
1                         05         957972           1945130   127.02455417   
2                         05         960701           1944850   127.05538008   
3                         01         961759           1944734   127.06735577   
4                         12         959356           1945637   127.04011999   
..                       ...              ...              ...           ...   
31                        12         914215           1503643   126.57623221   
32                        ##         895693           1490180   126.37837485   
33                        05         914158           1502613   126.57571727   
34                        12         897879           1499330   126.40067492   
35                        12         894876           1497277   126.36869771   

         la_crd  
0   37.49207623  
1   37.50449355  
2   37.50208078  
3   37.50107967  
4   37.50911605  
..          ...  
31  33.52125816  
32  33.39820124  
33  33.51196458  
34  33.48099758  
35  33.46202243  

[2662 rows x 23 columns]

In [6]:
import numpy as np
OBJT_ID=np.arange(len(df1))
df1['OBJT_ID']=OBJT_ID

In [7]:
df1=df1.astype(str)

In [8]:
df1.set_index("OBJT_ID",inplace=True)

In [9]:
df1

acc_year  occrrnc_dt dght_cd occrrnc_day_cd dth_dnv_cnt injpsn_cnt  \
OBJT_ID                                                                      
0           2022  2022021101       2              6           1          1   
1           2022  2022030919       2              4           1          1   
2           2022  2022031920       2              7           1          1   
3           2022  2022032606       1              7           1          2   
4           2022  2022040701       2              5           1          1   
...          ...         ...     ...            ...         ...        ...   
2657        2022  2022110618       2              1           1          1   
2658        2022  2022110908       1              4           1          1   
2659        2022  2022111515       1              3           1          1   
2660        2022  2022121909       1              2           1          1   
2661        2022  2022122007       1              3           1          1   

        se_dnv_cnt sl_dnv_cnt wnd_dnv_cnt occrrnc_lc_sido_cd  ... acc_ty_cd  \
OBJT_ID                                                       ...             
0                0          0           0               1100  ...        05   
1                0          0           0               1100  ...        22   
2                0          0           0               1100  ...        23   
3                1          0           0               1100  ...        22   
4                0          0           0               1100  ...        05   
...            ...        ...         ...                ...  ...       ...   
2657             0          0           0               2100  ...        01   
2658             0          0           0               2100  ...        32   
2659             0          0           0               2100  ...        25   
2660             0          0           0               2100  ...        05   
2661             0          0           0               2100  ...        02   

        aslt_vtr_cd road_frm_lclas_cd road_frm_cd wrngdo_isrty_vhcty_lclas_cd  \
OBJT_ID                                                                         
0               05                 01          05                          01   
1               03                 02          06                          02   
2               99                 01          05                          01   
3               03                 02          06                          02   
4               99                 02          06                          05   
...             ...               ...         ...                         ...   
2657            99                 01          05                          03   
2658            05                 01          05                          03   
2659            05                 01          05                          03   
2660            05                 01          05                          10   
2661            05                 02          06                          03   

        dmge_isrty_vhcty_lclas_cd occrrnc_lc_x_crd occrrnc_lc_y_crd  \
OBJT_ID                                                               
0                              12         962220           1943733    
1                              05         957972           1945130    
2                              05         960701           1944850    
3                              01         961759           1944734    
4                              12         959356           1945637    
...                           ...              ...              ...   
2657                           12         914215           1503643    
2658                           ##         895693           1490180    
2659                           05         914158           1502613    
2660                           12         897879           1499330    
2661                           12         894876           

In [11]:
import firebase_admin
from firebase_admin import credentials
from firebase_admin import firestore
import json
import pandas as pd

# Firebase 서비스 계정 키 파일 경로
cred = credentials.Certificate(".json")

# Firebase 앱 초기화
firebase_admin.initialize_app(cred)

db = firestore.client()

In [11]:
for col in df1.columns:
    doc_ref=db.collection('traffic').document(col)
    doc_ref.set(df1[col].to_dict())

In [12]:
docs=db.collection('traffic').stream()
data={}
for doc in docs:
    data[doc.id]=dict(sorted(doc.to_dict().items())).values()
sorted_df=pd.DataFrame(data, index=dict(sorted(doc.to_dict().items())).keys())
sorted_df

acc_ty_cd acc_ty_lclas_cd acc_ty_mlsfc_cd acc_year aslt_vtr_cd dght_cd  \
0           05              01              15     2022         05        2   
1           22              02              22     2022         03        2   
10          25              02              24     2022         03        1   
100         02              01              12     2022         05        2   
1000        01              01              11     2022         05        1   
...        ...             ...             ...      ...         ...     ...   
995         04              01              14     2022         99        1   
996         25              02              24     2022         05        2   
997         23              02              23     2022         05        1   
998         22              02              22     2022         06        2   
999         25              02              24     2022         05        1   

     dmge_isrty_vhcty_lclas_cd dth_dnv_cnt injpsn_cnt       la_crd  ...  \
0                           12           1          1  37.49207623  ...   
1                           05           1          1  37.50449355  ...   
10                          05           1          1  37.50155229  ...   
100                         12           1          1  37.48404544  ...   
1000                        12           1          1  37.71345947  ...   
...                        ...         ...        ...          ...  ...   
995                         12           1          1  37.37973712  ...   
996                         03           1          2  37.38291347  ...   
997                         03           1          3  37.39949456  ...   
998                         05           1          2  37.73130513  ...   
999                         01           1          1  37.70869045  ...   

     occrrnc_lc_sgg_cd occrrnc_lc_sido_cd occrrnc_lc_x_crd occrrnc_lc_y_crd  \
0                 1116               1100         962220           1943733    
1                 1116               1100         957972           1945130    
10                1116               1100         960567           1944792    
100               1114               1100         953351           1942887    
1000              1304               1300         960086           1968305    
...                ...                ...              ...              ...   
995               1336               1300         953244           1931315    
996               1336               1300         955703           1931654    
997               1336               1300         956003           1933492    
998               1304               1300         963313           1970270    
999               1304               1300         959445           1967779    

     road_frm_cd road_frm_lclas_cd se_dnv_cnt sl_dnv_cnt wnd_dnv_cnt  \
0             05                01          0          0           0   
1             06                02          0          0           0   
10            06                02          0          0           0   
100           06                02          0          0           0   
1000          07                02          0          0           0   
...          ...               ...        ...        ...         ...   
995           05                01          0          0           0   
996           05                01          0          1           0   
997           05                01          0          2           0   
998           06                02          0          1           0   
999           05                01          0          0           0   

     wrngdo_isrty_vhcty_lclas_cd  
0                             01  
1                             02  
10                            01  
100                           01  
1000                          03  
...                          ...  
995                           01  
996                           03  
997                       

In [15]:
import requests
import pandas as pd
import xmltodict
from os import name
import xml.etree.ElementTree as et
import bs4
from lxml import html
from urllib.parse import urlencode, quote_plus, unquote

df1=pd.DataFrame()

gugun=[1116,1117,1124,1111,1115,1123,1112,1125,1122,1107,1105,1114,1110,1109,1119,1104,1106,1118,1120,1113,1103,1108,1101,1102,1121,1212,1211,1216,1207,1203,1206,1208,1215,1210,1202,1214,1213,1204,1201,1205,1209,2204,2207,2208,2202,2205,2203,2206,2201,2309,2308,2303,2305,2302,2304,2306,2307,2310,2301,2404,2405,2401,2403,2402,2505,2501,2503,2504,2502,2602,2603,2604,2605,2601,2701,1322,1318,1332,1309,1319,1310,1333,1327,1334,1330,1306,1303,1302,1316,1307,1326,1305,1311,1323,1313,1320,1335,1325,1336,1304,1324,1317,1308,1321,1337,1315,1404,1422,1403,1407,1405,1420,1423,1415,1402,1421,1417,1418,1401,1406,1416,1412,1419,1413,1516,1520,1512,1514,1513,1517,1503,1521,1515,1511,1501,1502,1624,1605,1611,1615,1623,1604,1616,1606,1617,1603,1613,1621,1602,1619,1612,1620,1719,1702,1706,1705,1713,1720,1717,1711,1723,1715,1714,1701,1704,1712,1822,1818,1813,1808,1814,1806,1812,1802,1825,1819,1804,1832,1803,1828,1824,1830,1829,1821,1831,1827,1823,1820,1935,1903,1923,1906,1912,1904,1909,1932,1910,1924,1905,1917,1916,1907,1908,1930,1934,1933,1913,1922,1915,1925,1902,2010,2028,2022,2008,2024,2009,2023,2026,2016,2012,2003,2014,2030,2006,2025,2013,2027,2029,2102,2101]
url = "https://opendata.koroad.or.kr/data/rest/stt?authKey="
content=""
for i in gugun:
    params = {
    "searchYearCd":"2022",
    "sido":i-(i%100),
    "gugun":i,
    }
    response = requests.get(url, params=params)    
    content=content+response.text

    xml_obj = bs4.BeautifulSoup(content,'lxml-xml')
    rows = xml_obj.findAll('item')

    row_list = [] # 행값
    name_list = [] # 열이름값
    value_list = [] #데이터값

    # xml 안의 데이터 수집
    for i in range(0, len(rows)):
        columns = rows[i].find_all()
        #첫째 행 데이터 수집
        for j in range(0,len(columns)):
            if i ==0:
                # 컬럼 이름 값 저장
                name_list.append(columns[j].name)
            # 컬럼의 각 데이터 값 저장
            value_list.append(columns[j].text)
        # 각 행의 value값 전체 저장
        row_list.append(value_list)
        # 데이터 리스트 값 초기화
        value_list=[]

    #xml값 DataFrame으로 만들기
    df = pd.DataFrame(row_list, columns=name_list)
    df1=pd.concat([df1,df])
df1

std_year      acc_cl_nm sido_sgg_nm acc_cnt acc_cnt_cmrt dth_dnv_cnt  \
0      2022           전체사고   서울특별시 강남구    3709         1.88          16   
1      2022          어린이사고   서울특별시 강남구     111         1.21           2   
2      2022          고령자사고   서울특별시 강남구     414         1.15           4   
3      2022          보행자사고   서울특별시 강남구     782         2.08           7   
4      2022          자전거사고   서울특별시 강남구     140         1.11           1   
..      ...            ...         ...     ...          ...         ...   
8      2022        고령운전자사고   서울특별시 강남구     586         1.69           2   
9      2022        고령보행자사고   서울특별시 강남구      82         0.79           3   
10     2022  개인형이동수단(PM)사고   서울특별시 강남구      84         3.52           2   
11     2022          뺑소니사고   서울특별시 강남구      90         1.33           1   
12     2022          무면허사고   서울특별시 강남구      65         1.28           0   

   dth_dnv_cnt_cmrt ftlt_rate injpsn_cnt injpsn_cnt_cmrt  ... cnt_027_03  \
0              0.59      0.43       5052            1.79  ...        349   
1             11.11      1.80        123            1.08  ...       None   
2              0.32      0.97        442            1.13  ...       None   
3              0.75      0.90        795            2.09  ...       None   
4              0.53      0.71        155            1.18  ...       None   
..              ...       ...        ...             ...  ...        ...   
8              0.27      0.34        807            1.64  ...       None   
9              0.54      3.66         80            0.80  ...       None   
10             7.69      2.38         89            3.32  ...       None   
11             1.41      1.11        122            1.28  ...       None   
12             0.00      0.00         79            1.16  ...       None   

   cnt_027_04 cnt_027_05 cnt_027_06 cnt_027_07 cnt_027_99 cnt_014_01  \
0         474       2369        138        102        218        771   
1        None       None       None       None       None       None   
2        None       None       None       None       None       None   
3        None       None       None       None       None       None   
4        None       None       None       None       None       None   
..        ...        ...        ...        ...        ...        ...   
8        None       None       None       None       None       None   
9        None       None       None       None       None       None   
10       None       None       None       None       None       None   
11       None       None       None       None       None       None   
12       None       None       None       None       None       None   

   cnt_014_02 cnt_014_03 cnt_014_04  
0        2879         59          0  
1        None       None       None  
2        None       None       None  
3        None       None       None  
4        None       None       None  
..        ...        ...        ...  
8        None       None       None  
9        None       None       None  
10       None       None       None  
11       None       None       None  
12       None       None       None  

[3003 rows x 27 columns]

In [9]:
js = sorted_df.to_json(orient="columns",force_ascii=False)
js

'{"CTPRVN_CD":{"1":"11","10":"48","100":"11","1000":"41","1001":"41","1002":"41","1003":"41","1004":"41","1005":"41","1006":"41","1007":"41","1008":"41","1009":"41","101":"11","1010":"41","1011":"41","1012":"41","1013":"41","1014":"41","1015":"41","1016":"41","1017":"41","1018":"41","1019":"41","102":"11","1020":"41","1021":"41","1022":"41","1023":"41","1024":"41","1025":"41","1026":"41","1027":"41","1028":"41","1029":"41","103":"11","1030":"41","1031":"41","1032":"41","1033":"41","1034":"41","1035":"41","1036":"41","1037":"41","1038":"41","1039":"41","104":"11","1040":"41","1041":"41","1042":"41","1043":"41","1044":"41","1045":"41","1046":"41","1047":"41","1048":"41","1049":"41","105":"11","1050":"41","1051":"41","1052":"41","1053":"41","1054":"41","1055":"41","1056":"41","1057":"41","1058":"41","1059":"41","106":"11","1060":"41","1061":"41","1062":"41","1063":"41","1064":"41","1065":"41","1066":"41","1067":"41","1068":"41","1069":"41","107":"11","1070":"41","1071":"41","1072":"41","1

In [2]:
import numpy as np
np.arange(7)

array([0, 1, 2, 3, 4, 5, 6])

In [1]:
import json
with open("C:\sido.json",encoding='UTF8') as f:
    sido = json.load(f)
sido

{'type': 'FeatureCollection',
 'bbox': [124.7893155286271,
  33.172610584346295,
  130.96524575425667,
  38.54255349620522],
 'features': [{'type': 'Feature',
   'geometry': {'type': 'Polygon',
    'coordinates': [[[128.54880989370014, 38.301950820518755],
      [128.5600921732829, 38.25735515107489],
      [128.59761716763322, 38.21480959198724],
      [128.60765942875406, 38.15215810015938],
      [128.64206854447866, 38.106588627599855],
      [128.66939445927846, 38.08634208760778],
      [128.69458333244307, 38.0453480455091],
      [128.73326744935343, 38.01787054352603],
      [128.79463671088126, 37.92801060958252],
      [128.8233689458956, 37.90753318801803],
      [128.83001997197184, 37.88458455426084],
      [128.8786226699225, 37.8294251483049],
      [128.9852771172376, 37.74045442473868],
      [129.01482411622038, 37.70600771921262],
      [129.05505018456222, 37.675224044111836],
      [129.04353313092116, 37.642745963305245],
      [129.05392180246835, 37.62123228307

In [3]:
coordinates_dict = {}

# features 항목 반복
for feature in sido['features']:
    properties = feature['properties']
    geometry = feature['geometry']
    coordinates = geometry['coordinates'][0]  # Polygon의 경우 첫 번째 좌표 리스트를 사용
    
    # 필요한 속성 추출
    SIG_KOR_NM = properties['SIG_KOR_NM']
    
    # 경도와 위도를 따로 추출하여 딕셔너리로 만듦
    coordinates_dict[SIG_KOR_NM] = {coord[0]: coord[1] for coord in coordinates}

# DataFrame 생성
coordinates_dict

{'강원': {128.54880989370014: 38.301950820518755,
  128.5600921732829: 38.25735515107489,
  128.59761716763322: 38.21480959198724,
  128.60765942875406: 38.15215810015938,
  128.64206854447866: 38.106588627599855,
  128.66939445927846: 38.08634208760778,
  128.69458333244307: 38.0453480455091,
  128.73326744935343: 38.01787054352603,
  128.79463671088126: 37.92801060958252,
  128.8233689458956: 37.90753318801803,
  128.83001997197184: 37.88458455426084,
  128.8786226699225: 37.8294251483049,
  128.9852771172376: 37.74045442473868,
  129.01482411622038: 37.70600771921262,
  129.05505018456222: 37.675224044111836,
  129.04353313092116: 37.642745963305245,
  129.05392180246835: 37.62123228307141,
  129.11550878570839: 37.57855036235084,
  129.12163400699842: 37.52066201439543,
  129.18932196241568: 37.45204451034289,
  129.19776432627512: 37.41521414735909,
  129.2513233979134: 37.380088360708676,
  129.2506772120506: 37.362368874276115,
  129.28084694703435: 37.31347366301054,
  129.355278

In [4]:
def convert_values_to_string(data):
    if isinstance(data, dict):
        return {str(k): convert_values_to_string(v) for k, v in data.items()}
    elif isinstance(data, list):
        return [convert_values_to_string(elem) for elem in data]
    elif isinstance(data, tuple):
        return tuple(convert_values_to_string(elem) for elem in data)
    elif isinstance(data, str):
        return data  # 문자열인 경우 변환하지 않고 그대로 반환
    else:
        return str(data)  # 그 외의 경우에는 문자열로 변환

In [5]:
converted_data = convert_values_to_string(coordinates_dict)

In [8]:
db = firestore.client()
for SIG_KOR_NM, coordinates in converted_data.items():
    # 데이터 추가
    db.collection('sido').document(SIG_KOR_NM).set(coordinates)

In [1]:
import json
with open("C:\sig.json",encoding='UTF8') as f:
     sig= json.load(f)
sig

{'type': 'FeatureCollection',
 'bbox': [124.7893154389517,
  33.17261058239259,
  130.96325546758288,
  38.54261253850525],
 'features': [{'type': 'Feature',
   'geometry': {'type': 'Polygon',
    'coordinates': [[[127.60472638427933, 38.072648233869785],
      [127.60776133059719, 38.071674018579536],
      [127.65473867484185, 38.02576695898344],
      [127.65490464895771, 38.0272843475771],
      [127.73374753570245, 38.035814428263734],
      [127.73394342807514, 38.03607616237089],
      [127.77599099169834, 38.01389743776739],
      [127.77653868086756, 38.013597091144185],
      [127.77680464554413, 38.013645455050394],
      [127.77680679204794, 38.01364599945677],
      [127.77821827512304, 38.01390161291351],
      [127.78820556176866, 37.99429384493769],
      [127.85810008725723, 38.018823189046856],
      [127.84998445340655, 38.03881738462732],
      [127.84996624162804, 38.03970714676426],
      [127.85341448275034, 38.05051795468947],
      [127.85515517661896, 38.05230

In [10]:
coordinates_dict = {}

# features 항목 반복
for feature in sig['features']:
    properties = feature['properties']
    geometry = feature['geometry']
    coordinates = geometry['coordinates'][0]  # Polygon의 경우 첫 번째 좌표 리스트를 사용
    
    # 필요한 속성 추출
    SIG_KOR_NM = properties['SIG_KOR_NM']
    
    # 경도와 위도를 따로 추출하여 딕셔너리로 만듦
    coordinates_dict[SIG_KOR_NM] = {coord[0]: coord[1] for coord in coordinates}

# DataFrame 생성
coordinates_dict

{'춘천시': {127.60472638427933: 38.072648233869785,
  127.60776133059719: 38.071674018579536,
  127.65473867484185: 38.02576695898344,
  127.65490464895771: 38.0272843475771,
  127.73374753570245: 38.035814428263734,
  127.73394342807514: 38.03607616237089,
  127.77599099169834: 38.01389743776739,
  127.77653868086756: 38.013597091144185,
  127.77680464554413: 38.013645455050394,
  127.77680679204794: 38.01364599945677,
  127.77821827512304: 38.01390161291351,
  127.78820556176866: 37.99429384493769,
  127.85810008725723: 38.018823189046856,
  127.84998445340655: 38.03881738462732,
  127.84996624162804: 38.03970714676426,
  127.85341448275034: 38.05051795468947,
  127.85515517661896: 38.05230429633902,
  127.90267220658595: 38.05059746772935,
  127.90406646899208: 38.03033085142509,
  127.93819691986677: 38.0142189559451,
  127.95542737502664: 38.038681717354734,
  128.0266722331339: 38.017796712480774,
  128.02775769398346: 38.01662989632316,
  128.02960825528916: 38.01465092963498,
  12

In [11]:
converted_data = convert_values_to_string(coordinates_dict)

In [12]:
db = firestore.client()
for SIG_KOR_NM, coordinates in converted_data.items():
    # 데이터 추가
    db.collection('sig').document(SIG_KOR_NM).set(coordinates)

In [13]:
docs=db.collection('sido').stream()
def firestore_to_dict(collection_name):
    data_dict = {}
    # Firestore에서 데이터 가져오기
    docs = db.collection(collection_name).stream()
    for doc in docs:
        # 각 문서의 데이터를 딕셔너리로 변환하여 저장
        data_dict[doc.id] = doc.to_dict()
    return data_dict

# Firestore에서 'coordinates' 컬렉션의 데이터를 가져와서 딕셔너리로 변환
coordinates_dict = firestore_to_dict('sido')

# 결과 출력
coordinates_dict

{'강원': {'127.80046640044505': '37.43864051866462',
  '128.5837911134754': '37.08073706631039',
  '128.5992176998597': '37.08209460994004',
  '127.60903113525227': '37.64988237030668',
  '128.3815776656469': '37.15587131115258',
  '128.59554104110651': '37.08172115526072',
  '129.28084694703435': '37.31347366301054',
  '128.2409039329313': '37.227638014761474',
  '128.7552518181005': '37.0644535702407',
  '128.5688828453016': '37.08705854522273',
  '128.42300058335425': '37.10411649136583',
  '128.23702619398793': '37.22927777883599',
  '128.31535238229642': '37.196698833894764',
  '128.65238950466954': '37.065602054858005',
  '127.1489225708514': '38.24234375454817',
  '128.32988009563869': '37.20786183741896',
  '128.86503110159353': '37.0481300064702',
  '128.98417415532123': '37.08469362235354',
  '128.77005300686432': '37.07512976176954',
  '128.3111120152932': '37.14578388364735',
  '128.39106769653094': '37.15512131216391',
  '127.86081375264055': '38.28255443372146',
  '128.7742

In [2]:
import pandas as pd
data = []
for feature in sido['features']:
    coordinates = feature['geometry']['coordinates'][0]
    SIG_KOR_NM = feature['properties']['SIG_KOR_NM']
    for coord in coordinates:
        lon, lat = coord
        data.append({'SIG_KOR_NM': SIG_KOR_NM, 'Longitude': str(lon), 'Latitude': str(lat)})

# DataFrame 생성
df = pd.DataFrame(data)

# 결과 출력
print(df)

     SIG_KOR_NM           Longitude            Latitude
0            강원  128.54880989370014  38.301950820518755
1            강원   128.5600921732829   38.25735515107489
2            강원  128.59761716763322   38.21480959198724
3            강원  128.60765942875406   38.15215810015938
4            강원  128.64206854447866  38.106588627599855
...         ...                 ...                 ...
8270         광주  126.74203664978286  35.251305541901225
8271         광주  126.74246154737597   35.25196020983384
8272         광주  126.74258923537597  35.252137649849246
8273         광주  126.74259214600683  35.251166609324166
8274         광주  126.76104901664232  35.258570431400145

[8275 rows x 3 columns]


In [3]:
import numpy as np
OBJT_ID=np.arange(len(df))
df['OBJT_ID']=OBJT_ID

In [5]:
df=df.astype(str)

In [7]:
df.set_index("OBJT_ID",inplace=True)

In [8]:
df

SIG_KOR_NM           Longitude            Latitude
OBJT_ID                                                   
0               강원  128.54880989370014  38.301950820518755
1               강원   128.5600921732829   38.25735515107489
2               강원  128.59761716763322   38.21480959198724
3               강원  128.60765942875406   38.15215810015938
4               강원  128.64206854447866  38.106588627599855
...            ...                 ...                 ...
8270            광주  126.74203664978286  35.251305541901225
8271            광주  126.74246154737597   35.25196020983384
8272            광주  126.74258923537597  35.252137649849246
8273            광주  126.74259214600683  35.251166609324166
8274            광주  126.76104901664232  35.258570431400145

[8275 rows x 3 columns]

In [11]:
for col in df.columns:
    doc_ref=db.collection('sido').document(col)
    doc_ref.set(df[col].to_dict())

In [12]:
docs=db.collection('sido').stream()
data={}
for doc in docs:
    data[doc.id]=dict(sorted(doc.to_dict().items())).values()
sorted_df=pd.DataFrame(data, index=dict(sorted(doc.to_dict().items())).keys())
sorted_df

Latitude           Longitude SIG_KOR_NM
0     38.301950820518755  128.54880989370014         강원
1      38.25735515107489   128.5600921732829         강원
10     37.88458455426084  128.83001997197184         강원
100    37.09212064413647  128.92319827326182         강원
1000   37.18928064496871  128.03720306560032         강원
...                  ...                 ...        ...
995     37.2453766796712   128.2120658419042         강원
996    37.23260505841317  128.17409861245437         강원
997   37.213308702545994  128.16404062128265         강원
998    37.23453731924993   128.1253222358382         강원
999    37.20767155165618  128.11150413136116         강원

[8275 rows x 3 columns]

In [24]:
sorted_df.index=sorted_df.index.astype(int)
sorted_df=sorted_df.sort_index()
sorted_df

Latitude           Longitude SIG_KOR_NM
0     38.301950820518755  128.54880989370014         강원
1      38.25735515107489   128.5600921732829         강원
2      38.21480959198724  128.59761716763322         강원
3      38.15215810015938  128.60765942875406         강원
4     38.106588627599855  128.64206854447866         강원
...                  ...                 ...        ...
8270  35.251305541901225  126.74203664978286         광주
8271   35.25196020983384  126.74246154737597         광주
8272  35.252137649849246  126.74258923537597         광주
8273  35.251166609324166  126.74259214600683         광주
8274  35.258570431400145  126.76104901664232         광주

[8275 rows x 3 columns]

In [2]:
import pandas as pd
data = []
for feature in sig['features']:
    coordinates = feature['geometry']['coordinates'][0]
    SIG_KOR_NM = feature['properties']['SIG_KOR_NM']
    for coord in coordinates:
        lon, lat = coord
        data.append({'SIG_KOR_NM': SIG_KOR_NM, 'Longitude': str(lon), 'Latitude': str(lat)})

# DataFrame 생성
df = pd.DataFrame(data)

# 결과 출력
print(df)

      SIG_KOR_NM           Longitude            Latitude
0            춘천시  127.60472638427933  38.072648233869785
1            춘천시  127.60776133059719  38.071674018579536
2            춘천시  127.65473867484185   38.02576695898344
3            춘천시  127.65490464895771    38.0272843475771
4            춘천시  127.73374753570245  38.035814428263734
...          ...                 ...                 ...
33736        단양군  128.33067274397132  37.150343161959555
33737        단양군   128.3321861018014   37.15157272967114
33738        단양군   128.3362324236008  37.157571891745874
33739        단양군  128.33709310123746   37.15785242764599
33740        단양군  128.33948214774796   37.15799442842731

[33741 rows x 3 columns]


In [3]:
import numpy as np
OBJT_ID=np.arange(len(df))
df['OBJT_ID']=OBJT_ID

In [4]:
df=df.astype(str)

In [5]:
df.set_index("OBJT_ID",inplace=True)

In [6]:
df

SIG_KOR_NM           Longitude            Latitude
OBJT_ID                                                   
0              춘천시  127.60472638427933  38.072648233869785
1              춘천시  127.60776133059719  38.071674018579536
2              춘천시  127.65473867484185   38.02576695898344
3              춘천시  127.65490464895771    38.0272843475771
4              춘천시  127.73374753570245  38.035814428263734
...            ...                 ...                 ...
33736          단양군  128.33067274397132  37.150343161959555
33737          단양군   128.3321861018014   37.15157272967114
33738          단양군   128.3362324236008  37.157571891745874
33739          단양군  128.33709310123746   37.15785242764599
33740          단양군  128.33948214774796   37.15799442842731

[33741 rows x 3 columns]

In [7]:
num=len(df)
middle=num//2
df1=df.iloc[:middle]
df2=df.iloc[middle:]

In [16]:
for col in df1.columns:
    doc_ref=db.collection('sig1').document(col)
    doc_ref.set(df1[col].to_dict())

In [18]:
for col in df2.columns:
    doc_ref=db.collection('sig2').document(col)
    doc_ref.set(df2[col].to_dict())

In [20]:
docs=db.collection('sig1').stream()
data={}
for doc in docs:
    data[doc.id]=dict(sorted(doc.to_dict().items())).values()
sorted_df1=pd.DataFrame(data, index=dict(sorted(doc.to_dict().items())).keys())
sorted_df1

Latitude           Longitude SIG_KOR_NM
0     38.072648233869785  127.60472638427933        춘천시
1     38.071674018579536  127.60776133059719        춘천시
10     38.01390161291351  127.77821827512304        춘천시
100   37.282447130296816  128.17769075160652        원주시
1000   37.24826062207418  128.57103556746156        영월군
...                  ...                 ...        ...
9995  35.373472585036595  128.10315092003492        의령군
9996  35.373778259005476  128.10341564729976        의령군
9997  35.373886126347585  128.10350437783626        의령군
9998  35.374309984254516  128.10372652237186        의령군
9999   35.37436786738755  128.10376811533172        의령군

[16870 rows x 3 columns]

In [21]:
docs=db.collection('sig2').stream()
data={}
for doc in docs:
    data[doc.id]=dict(sorted(doc.to_dict().items())).values()
sorted_df2=pd.DataFrame(data, index=dict(sorted(doc.to_dict().items())).keys())
sorted_df2

Latitude           Longitude SIG_KOR_NM
16870   36.36398276173377  127.36519437708915        유성구
16871   36.35870193027713  127.35850356472568        유성구
16872    36.3579964586429  127.35825943257312        유성구
16873   36.32904444274447  127.33590314807691        유성구
16874   36.47579777364857  127.48423140565102        대덕구
...                   ...                 ...        ...
33736  37.150343161959555  128.33067274397132        단양군
33737   37.15157272967114   128.3321861018014        단양군
33738  37.157571891745874   128.3362324236008        단양군
33739   37.15785242764599  128.33709310123746        단양군
33740   37.15799442842731  128.33948214774796        단양군

[16871 rows x 3 columns]

In [22]:
sorted_df=pd.concat([sorted_df1,sorted_df2])

Latitude           Longitude SIG_KOR_NM
0      38.072648233869785  127.60472638427933        춘천시
1      38.071674018579536  127.60776133059719        춘천시
10      38.01390161291351  127.77821827512304        춘천시
100    37.282447130296816  128.17769075160652        원주시
1000    37.24826062207418  128.57103556746156        영월군
...                   ...                 ...        ...
33736  37.150343161959555  128.33067274397132        단양군
33737   37.15157272967114   128.3321861018014        단양군
33738  37.157571891745874   128.3362324236008        단양군
33739   37.15785242764599  128.33709310123746        단양군
33740   37.15799442842731  128.33948214774796        단양군

[33741 rows x 3 columns]

In [23]:
sorted_df.index=sorted_df.index.astype(int)
sorted_df=sorted_df.sort_index()
sorted_df

Latitude           Longitude SIG_KOR_NM
0      38.072648233869785  127.60472638427933        춘천시
1      38.071674018579536  127.60776133059719        춘천시
2       38.02576695898344  127.65473867484185        춘천시
3        38.0272843475771  127.65490464895771        춘천시
4      38.035814428263734  127.73374753570245        춘천시
...                   ...                 ...        ...
33736  37.150343161959555  128.33067274397132        단양군
33737   37.15157272967114   128.3321861018014        단양군
33738  37.157571891745874   128.3362324236008        단양군
33739   37.15785242764599  128.33709310123746        단양군
33740   37.15799442842731  128.33948214774796        단양군

[33741 rows x 3 columns]